# Uninstalling the clean rooms native app from your Snowflake account

This notebook helps you uninstall the Snowflake Data Clean Rooms application for your entire account. This notebook should be used as part of the uninstallation flow described in the [clean rooms documentation](https://docs.snowflake.com/en/user-guide/cleanrooms/uninstalling-clean-rooms) to uninstall clean rooms from your Snowflake account.

Many of the steps below generate a list of commands that should be run in the following cell. Copy the cell output and run them in the next cell as described.

This notebook must be run in the account where you want to uninstall the clean room environment, and you must use the ACCOUNTADMIN role.

In [ ]:
USE ROLE ACCOUNTADMIN;

## 1. Drop listings

In [ ]:
-- Generate SQL drop commands.

SHOW listings;
WITH listings AS (
    SELECT * FROM TABLE(result_scan(last_query_id()))
    WHERE "name" ilike 'SAMOOHA^_CLEANROOM^_%' ESCAPE '^'
),
alter_n_drop_listings AS (
    SELECT 'ALTER LISTING ' || "name" || ' UNPUBLISH;DROP LISTING ' || "name" || ';'
    FROM listings WHERE "state" = 'PUBLISHED'
),
drop_listings AS (
    SELECT 'DROP LISTING ' || "name" || ';'
    FROM listings WHERE "state" = 'UNPUBLISHED'
)
SELECT * FROM alter_n_drop_listings
UNION ALL
SELECT * FROM drop_listings;

In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

## 2. Drop shares

In [ ]:
-- Generate SQL drop commands.

SHOW SHARES;
SELECT CONCAT('DROP SHARE ', "name", ';')
  FROM TABLE(RESULT_SCAN(last_query_id()))
  WHERE "kind" = 'OUTBOUND'
    AND "name" LIKE 'SAMOOHA_CLEANROOM_%';


In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

In [ ]:
-- These shares have to be dropped manually:
DROP SHARE SAMOOHA_INTERNAL_GOVERNANCE_SUMMARY_SHARE_NAV2;
DROP SHARE SAMOOHA_INTERNAL_LOGS_SHARE_NAV2;
DROP SHARE SAMOOHA_INTERNAL_PROVIDER_METADATA_NAV2;

## 3. Drop LAF

If you have enabled cross-cloud auto-fulfillment in your account, must  uninstall the resources associated with that feature. If the procedure in the following cell returns TRUE, then continue with this step; if procedure returns FALSE, then skip to step 4, _Drop applications_.

In [ ]:
-- If the following procedure returns TRUE, you need to uninstall
-- your cross-cloud resources. If it returns FALSE, you can skip to
-- the drop applications step.
CALL samooha_by_snowflake_local_db.library.is_laf_enabled_on_account();

In [ ]:
-- Add the account name to the next cell as indicated.
CALL current_account();

In [ ]:
-- Replace the placeholder below with your account name from the previous cell.
SET listing_name = CONCAT ('SAMOOHA_INTERNAL_GOVERNANCE_SUMMARY_SHARE_NAV2_LAF_','<current account name>');

-- Sanity check to ensure that you got the listing name correct.
-- If this fails, check your syntax.
DESC LISTING IDENTIFIER($listing_name);

In [ ]:
-- Now drop the listing
ALTER LISTING IDENTIFIER($listing_name) UNPUBLISH;
DROP LISTING IDENTIFIER($listing_name);

In [ ]:
-- Generate SQL drop commands.

SHOW REPLICATION GROUPS ->>
SELECT
  "name" AS name,
  "comment" AS comment,
  "is_primary" AS is_primary,
  "primary" AS primary,
  "secondary_state" AS secondary_state
  FROM $1
    WHERE comment LIKE
      '%SAMOOHA_INTERNAL_GOVERNANCE_SUMMARY_SHARE_NAV2_LAF%';  
SELECT
  CONCAT('GRANT OWNERSHIP ON REPLICATION GROUP ',
         "NAME",
         ' TO ROLE ACCOUNTADMIN REVOKE CURRENT GRANTS;
           DROP REPLICATION GROUP ', 
         "NAME",';')  
  FROM TABLE(RESULT_SCAN(last_query_id())); 

In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

In [ ]:
DROP SHARE SAMOOHA_INTERNAL_GOVERNANCE_SUMMARY_SHARE_NAV2_LAF;

## 4. Drop applications

In [ ]:
-- Generate SQL drop commands.

SHOW APPLICATIONS;
SELECT CONCAT('DROP APPLICATION ', "name", ' CASCADE;')
  FROM TABLE(RESULT_SCAN(last_query_id()))
  WHERE "name" LIKE 'SAMOOHA_CLEANROOM_APP_%';


In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

## 5. Drop application packages

In [ ]:
-- Generate SQL drop commands.

SHOW APPLICATION PACKAGES;
SELECT CONCAT('DROP APPLICATION PACKAGE ', "name", ' CASCADE;')
  FROM TABLE(RESULT_SCAN(last_query_id())) WHERE "name" LIKE 'SAMOOHA_CLEANROOM_%';

In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

## 6. Drop databases

In [ ]:
-- Generate SQL drop commands.

SHOW DATABASES;
SELECT CONCAT('DROP DATABASE ', "name", ';')
  FROM TABLE(RESULT_SCAN(last_query_id()))
  WHERE "name" = 'SAMOOHA_SAMPLE_DATABASE'
    OR "name" LIKE 'SAMOOHA_CLEANROOM_%'
    OR "name" = 'SAMOOHA_BY_SNOWFLAKE_LOCAL_DB'
    OR "name" LIKE 'SAMOOHA_INTERNAL_GOVERNANCE_%'
    AND NOT startswith("name", 'SAMOOHA_CLEANROOM_CONSUMER_');

In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

## 7. Drop warehouses

In [ ]:
-- Generate SQL drop commands.

SHOW WAREHOUSES;
SELECT 'DROP WAREHOUSE IF EXISTS ' || "name" || ';' AS drop_statements
FROM TABLE(RESULT_SCAN(LAST_QUERY_ID()))
WHERE "name" LIKE 'APP\_WH%'
  OR "name" LIKE 'DCR\_WH%'
  OR "name" LIKE 'PROVIDER\_RUN\_%'
  OR "name" LIKE 'SAMOOHA_TASK_WAREHOUSE'
ORDER BY "name";

In [ ]:
-- Paste and run the statements generated by the previous cell here.
...

## Drop the Snowflake Data Clean Rooms native application

This is the last step in deleting the native application from your account.

In [ ]:
DROP APPLICATION SAMOOHA_BY_SNOWFLAKE CASCADE;